In [ ]:
import random
import numpy as np
import pandas as pd
import statsmodels.api as sm
import plotly.graph_objects as go

from scipy.stats import norm, lognorm, truncnorm, gaussian_kde
from plotly.subplots import make_subplots
from scipy.integrate import quad

import math

import matplotlib.pyplot as plt

In [ ]:
mu    = 2
sigma = 0.5

num_of_samples      = 100
num_of_MCMC_samples = 10000

x = np.linspace(0.01, 100, 10000)

In [ ]:
def p(x):
    return norm.pdf(x, loc=mu, scale=sigma)

def q(x):
    return norm.pdf(x, loc=mu+1, scale=sigma)

def f(x):
    return norm.cdf(x, loc=mu+1, scale=sigma)

In [ ]:
def integrand(x):
    return p(x) * f(x)

def get_MC_samples(num_of_samples): 
    return norm.rvs(loc=mu, scale=sigma, size=num_of_samples)

def get_MC_estimate(num_of_samples, function):         
    return 1./num_of_samples * np.sum(function)

def get_trunc_MC_samples(num_of_samples, lower_bound):
    samples = []
    while len(samples) < num_of_samples:
        sample = norm.rvs(loc=mu, scale=sigma, size=1)
        if sample >= lower_bound:
            samples.append(sample[0])
    return np.array(samples)

def get_IS_samples(num_of_samples): 
    return norm.rvs(loc=mu+1, scale=sigma, size=num_of_samples)

def get_IS_estimate(num_of_samples, samples):         
    return 1./num_of_samples * np.sum(f(samples)*p(samples)/q(samples))

def get_MCMC_samples(num_of_samples, mu, sigma, initial_sigma):

    sample = [0 for n in range(num_of_samples)]
    function = [0 for n in range(num_of_samples)]

    sample[0] = norm.rvs(loc=mu, scale=sigma, size=1)[0]    
    function[0] = f(sample[0])  

    for n in range(1, num_of_samples):          
        proposal_sigma = 0.5*((num_of_samples-n)/num_of_samples)+initial_sigma
        
        candidate_sample = np.random.normal(sample[n-1], proposal_sigma, 1)[0]
        function[n] = f(candidate_sample)  

        prob_of_previous_sample = p(sample[n-1])
        prob_of_candidate_sample = p(candidate_sample)

        prob_of_previous_given_candidate = norm.pdf(sample[n-1], loc=candidate_sample, scale=proposal_sigma)
        prob_of_candidate_given_previous = norm.pdf(candidate_sample, loc=sample[n-1], scale=proposal_sigma)

        acceptance_ratio = (function[n] * prob_of_candidate_sample * prob_of_previous_given_candidate) / (function[n-1] * prob_of_previous_sample * prob_of_candidate_given_previous)
        if random.uniform(0, 1) < acceptance_ratio:
            sample[n] = candidate_sample
        else:
            sample[n] = sample[n-1]
            function[n] = function[n-1]

    samples = sample[:]
    return samples, function

In [ ]:
true_value, _ = quad(integrand, 0, np.inf)
true_value

0.07864960352512981

In [ ]:
MC_samples = get_MC_samples(num_of_samples)
MC_f_of_x  = f(MC_samples)

MC_estimate = np.average(MC_f_of_x)
MC_error    = np.average(np.abs(f(MC_samples)-true_value)/true_value)

print('MC Estimate =', MC_estimate)
print('MC Relative Error =', MC_error)

MC Estimate = 0.05763732449987713
MC Relative Error = 0.9983698306392276


In [ ]:
trunc_MC_samples = get_trunc_MC_samples(num_of_samples, 3)
trunc_MC_f_of_x  = f(trunc_MC_samples)

trunc_MC_estimate = np.mean(trunc_MC_f_of_x)
trunc_MC_error   = np.average(np.abs(f(trunc_MC_samples)-true_value)/true_value)

print('Truncated MC Estimate =', trunc_MC_estimate)
print('TruncatedMC Relative Error =', trunc_MC_error)

Truncated MC Estimate = 0.6274331356612902
TruncatedMC Relative Error = 6.977575315568058


In [ ]:
IS_samples  = get_IS_samples(num_of_samples)
IS_f_of_x   = f(IS_samples)*p(IS_samples)/q(IS_samples)
IS_estimate = get_IS_estimate(num_of_samples, IS_samples)
IS_error    = np.average(np.abs(IS_f_of_x-true_value)/true_value)

print('IS Estimate =', IS_estimate)
print('IS Relative Error =', IS_error)

IS Estimate = 0.08581257554984272
IS Relative Error = 0.677396544949367


In [ ]:
MCMC_samples, MCMC_f_of_x = get_MCMC_samples(num_of_MCMC_samples, mu, sigma, sigma)
kde = gaussian_kde(np.array(MCMC_samples).T, bw_method = 'silverman')

MCMC_IS_samples = kde.resample(num_of_samples)[0]
pp = p(MCMC_IS_samples)
qq = kde.evaluate(MCMC_IS_samples)
ff = f(MCMC_IS_samples)

MCMC_IS_estimate = np.average((pp/qq)*ff)
MCMC_IS_error    = np.average(np.abs((pp/qq)*ff-true_value)/true_value)

print('MCMC_IS Estimate =', MCMC_IS_estimate)
print('MCMC_IS Error =', MCMC_IS_error)

MCMC_IS Estimate = 0.0784417605739476
MCMC_IS Error = 0.031963491097017134


In [ ]:
fig = go.Figure()
fig.update_layout(
    xaxis=dict(
        showline=True, zeroline=True, linewidth=2, linecolor='black', mirror = True,
        showgrid=False, showticklabels=True, ticks="outside", tickfont=dict(size=15, family="times new roman", color='black'),
        title='Hazard Intensity - x', titlefont=dict(size=18, family="times new roman", color='black'),
        range=[0, 5]),
    yaxis=dict(
        showline=True, zeroline=True, linewidth=2, linecolor='black', mirror= True, side="left",
        showgrid=True, showticklabels=True, ticks="outside", tickfont_size=15,
        title='Loss Function - f(x)', titlefont=dict(size=18, family="times new roman", color='black'),  
        range=[0, 1]),
    yaxis2=dict(
        showline=True, zeroline=False, linewidth=2, linecolor='black',
        showgrid=False, showticklabels=False, 
        range=[0, 0.9]),
    showlegend = True,
    legend_font=dict(
        family="Times New Roman",
        size=18,
        color="black"),
    paper_bgcolor = 'rgba(0,0,0,0)',
    plot_bgcolor  = 'rgba(0,0,0,0)',
    height = 500,
    width  = 800)

fig.add_scatter(x=x, y=f(x), line=dict(dash='dot', color='black'), yaxis='y', name='f(x)')
fig.add_scatter(x=x, y=p(x),  line=dict(color='blue'), yaxis='y2', name='p(x)')

fig.add_vrect(
        x0=4, y0=0,
        x1=5, y1=1,
        fillcolor='gray',
        opacity=0.2,
        line_width=0.1,
        line_color='black')
    
fig.show()
# fig.write_image("f&p.png", width=800, height=500)


In [ ]:
fig = go.Figure()
fig.update_layout(
    xaxis=dict(
        showline=True, zeroline=True, linewidth=2, linecolor='black', mirror = True,
        showgrid=False, showticklabels=True, ticks="outside", tickfont=dict(size=15, family="times new roman", color='black'),
        title='Hazard Intensity - x', titlefont=dict(size=18, family="times new roman", color='black'),
        range=[0, 5]),
    yaxis=dict(
        showline=True, zeroline=True, linewidth=2, linecolor='black', mirror= True, side="left",
        showgrid=True, showticklabels=True, ticks="outside", tickfont_size=15,
        title='Loss Function - f(x)', titlefont=dict(size=18, family="times new roman", color='black'),  
        range=[0, 1]),
    yaxis2=dict(
        showline=True, zeroline=False, linewidth=2, linecolor='black',
        showgrid=False, showticklabels=False, 
        range=[0, 0.9]),
    showlegend = True,
    legend_font=dict(
        family="Times New Roman",
        size=18,
        color="black"),
    paper_bgcolor = 'rgba(0,0,0,0)',
    plot_bgcolor  = 'rgba(0,0,0,0)',
    height = 500,
    width  = 800)

fig.add_scatter(x=x, y=f(x), line=dict(dash='dot', color='black'), yaxis='y', name='f(x)')
fig.add_scatter(x=x, y=p(x),  line=dict(color='blue'), yaxis='y2', name='p(x)')
fig.add_scatter(x=x, y=p(x)*f(x), line=dict(dash='dash', color='gray'), fill='tozeroy', yaxis='y2', name='f(x)p(x)')

fig.add_scatter(x=[0, norm.ppf(true_value, loc=mu+1, scale=sigma)], y=[true_value, 0],
                line=dict(shape='hv', color='green', width=3, dash='dash'), marker=dict(opacity=0), 
                name='True Value')

# Add the text trace
fig.add_trace(go.Scatter(x=[1.5], y=[true_value + 0.05], 
                         mode='text',
                         text=[f'True Value = {np.round(true_value, 4)}'],
                         textfont=dict(family="times new roman", size=18, color='green'), showlegend=False))

fig.show()
# fig.write_image("true_value.png")

In [ ]:
fig = go.Figure()
fig.update_layout(
    xaxis=dict(
        showline=True, zeroline=True, linewidth=2, linecolor='black', mirror = True,
        showgrid=False, showticklabels=True, ticks="outside", tickfont=dict(size=15, family="times new roman", color='black'),
        title='Hazard Intensity - x', titlefont=dict(size=18, family="times new roman", color='black'),
        range=[0, 5]),
    yaxis=dict(
        showline=True, zeroline=True, linewidth=2, linecolor='black', mirror= True, side="left",
        showgrid=True, showticklabels=True, ticks="outside", tickfont_size=15,
        title='Loss Function - f(x)', titlefont=dict(size=18, family="times new roman", color='black'),  
        range=[0, 1]),
    yaxis2=dict(
        showline=True, zeroline=False, linewidth=2, linecolor='black',
        showgrid=False, showticklabels=False, 
        range=[0, 0.9]),
    showlegend = True,
    legend_font=dict(
        family="Times New Roman",
        size=18,
        color="black"),
    paper_bgcolor = 'rgba(0,0,0,0)',
    plot_bgcolor  = 'rgba(0,0,0,0)',
    height = 500,
    width  = 800)

fig.add_scatter(x=x, y=f(x), line=dict(dash='dot', color='black'), yaxis='y', name='f(x)')
fig.add_scatter(x=x, y=p(x),  line=dict(color='blue'), yaxis='y2', name='p(x)')

for i in range(len(MC_samples)):
    trace = go.Scatter(
        x=[MC_samples[i], -1],
        y=[0, MC_f_of_x[i]],
        line_shape='vh',
        line=dict(color='black', width=0.3),
        marker=dict(size=18, symbol='line-ns', line=dict(width=2.5, color="DarkSlateGrey")),
        showlegend = False)   
    fig.add_trace(trace)

fig.add_scatter(x=[0], y=[np.average(MC_f_of_x)], mode='markers+text', 
                marker=dict(size=30, symbol='line-ew-open', line=dict(width=4.5, color='black')), 
                text = f'E[f(x)] = {np.round(np.average(MC_f_of_x), 4)}', textposition="top right", 
                textfont=dict(family="times new roman", size=15, color='black'), showlegend=False)

fig.add_scatter(x=[0, norm.ppf(true_value, loc=mu+1, scale=sigma)], y=[true_value, 0],  
                line=dict(shape='hv', color='green', width=3, dash='dash'), marker=dict(opacity=0),  
                name='True Value')
    
fig.show()
# fig.write_image("crude_MC_samples.png")

In [ ]:
fig = go.Figure()
fig.update_layout(
    xaxis=dict(
        showline=True, zeroline=True, linewidth=2, linecolor='black', mirror = True,
        showgrid=False, showticklabels=True, ticks="outside", tickfont=dict(size=15, family="times new roman", color='black'),
        title='Hazard Intensity - x', titlefont=dict(size=18, family="times new roman", color='black'),
        range=[0, 5]),
    yaxis=dict(
        showline=True, zeroline=True, linewidth=2, linecolor='black', mirror= True, side="left",
        showgrid=True, showticklabels=True, ticks="outside", tickfont_size=15,
        title='Loss Function - f(x)', titlefont=dict(size=18, family="times new roman", color='black'),  
        range=[0, 1]),
    yaxis2=dict(
        showline=True, zeroline=False, linewidth=2, linecolor='black',
        showgrid=False, showticklabels=False, 
        range=[0, 0.9]),
    showlegend = True,
    legend_font=dict(
        family="Times New Roman",
        size=18,
        color="black"),
    paper_bgcolor = 'rgba(0,0,0,0)',
    plot_bgcolor  = 'rgba(0,0,0,0)',
    height = 500,
    width  = 800)

fig.add_scatter(x=x, y=f(x), line=dict(dash='dot', color='black'), yaxis='y', name='f(x)')
fig.add_scatter(x=x, y=p(x),  line=dict(color='blue'), yaxis='y2', name='p(x)')

for i in range(len(trunc_MC_samples)):
    trace = go.Scatter(
        x=[trunc_MC_samples[i], -1],
        y=[0, trunc_MC_f_of_x[i]],
        line_shape='vh',
        line=dict(color='black', width=0.3),
        marker=dict(size=18, symbol='line-ns', line=dict(width=2.5, color="DarkSlateGrey")),
        showlegend = False)   
    fig.add_trace(trace)

fig.add_scatter(x=[0], y=[np.average(trunc_MC_f_of_x)], mode='markers+text', 
                marker=dict(size=30, symbol='line-ew', line=dict(width=4.5, color='black')), 
                text = f'E[f(x)] = {np.round(np.average(trunc_MC_f_of_x), 4)}', textposition="top right", 
                textfont=dict(family="times new roman", size=15, color='black'),
                showlegend=False)

fig.add_scatter(x=[0, norm.ppf(true_value, loc=mu+1, scale=sigma)], y=[true_value, 0],  
                line=dict(shape='hv', color='green', width=3, dash='dash'), marker=dict(opacity=0),  
                name='True Value')
    
fig.show()
# fig.write_image("truncated_MC_samples.png")

In [ ]:
fig = go.Figure()
fig.update_layout(
    xaxis=dict(
        showline=True, zeroline=True, linewidth=2, linecolor='black', mirror = True,
        showgrid=False, showticklabels=True, ticks="outside", tickfont=dict(size=15, family="times new roman", color='black'),
        title='Hazard Intensity - x', titlefont=dict(size=18, family="times new roman", color='black'),
        range=[0, 5]),
    yaxis=dict(
        showline=True, zeroline=True, linewidth=2, linecolor='black', mirror= True, side="left",
        showgrid=True, showticklabels=True, ticks="outside", tickfont_size=15,
        title='Loss Function - f(x)', titlefont=dict(size=18, family="times new roman", color='black'),  
        range=[0, 1]),
    yaxis2=dict(
        showline=True, zeroline=False, linewidth=2, linecolor='black',
        showgrid=False, showticklabels=False, 
        range=[0, 0.9]),
    showlegend = True,
    legend_font=dict(
        family="Times New Roman",
        size=18,
        color="black"),
    paper_bgcolor = 'rgba(0,0,0,0)',
    plot_bgcolor  = 'rgba(0,0,0,0)',
    height = 500,
    width  = 800)

fig.add_scatter(x=x, y=f(x), line=dict(dash='dot', color='black'), yaxis='y', name='f(x)')
fig.add_scatter(x=x, y=p(x),  line=dict(color='blue'), yaxis='y2', name='p(x)')
fig.add_scatter(x=x, y=q(x),  line=dict(dash='dash', color='blue'), yaxis='y2', name='q(x)')

fig.show()
# fig.write_image("IS_dist.png")

In [ ]:
fig = go.Figure()
fig.update_layout(
    xaxis=dict(
        showline=True, zeroline=True, linewidth=2, linecolor='black', mirror = True,
        showgrid=False, showticklabels=True, ticks="outside", tickfont=dict(size=15, family="times new roman", color='black'),
        title='Hazard Intensity - x', titlefont=dict(size=18, family="times new roman", color='black'),
        range=[0, 5]),
    yaxis=dict(
        showline=True, zeroline=True, linewidth=2, linecolor='black', mirror= True, side="left",
        showgrid=True, showticklabels=True, ticks="outside", tickfont_size=15,
        title='Loss Function - f(x)', titlefont=dict(size=18, family="times new roman", color='black'),  
        range=[0, 1]),
    yaxis2=dict(
        showline=True, zeroline=False, linewidth=2, linecolor='black',
        showgrid=False, showticklabels=False, 
        range=[0, 0.9]),
    showlegend = True,
    legend_font=dict(
        family="Times New Roman",
        size=18,
        color="black"),
    paper_bgcolor = 'rgba(0,0,0,0)',
    plot_bgcolor  = 'rgba(0,0,0,0)',
    height = 500,
    width  = 800)

fig.add_scatter(x=x, y=f(x)*p(x)/q(x), line=dict(dash='dot', color='black'), yaxis='y', name='f(x)p(x)/q(x)')
fig.add_scatter(x=x, y=q(x),  line=dict(dash='dash', color='blue'), yaxis='y2', name='q(x)')

for i in range(len(IS_samples)):
    trace = go.Scatter(
        x=[IS_samples[i], 0],
        y=[0, IS_f_of_x[i]],
        line_shape='vh',
        line=dict(color='black', width=0.3),
        marker=dict(size=18, symbol='line-ns', line=dict(width=2.5, color="DarkSlateGrey")),
        showlegend = False)
    
    fig.add_trace(trace)

fig.add_scatter(x=[0], y=[np.average(IS_f_of_x)], mode='markers+text',
                marker=dict(size=30, symbol='line-ew', line=dict(width=4.5, color='black')),
                text=f'E[f(x)] = {np.round(np.average(IS_f_of_x), 4)}', textposition="top right",
                textfont=dict(family="times new roman", size=15, color='black'), showlegend=False)

fig.add_scatter(x=[0, norm.ppf(true_value, loc=mu+1, scale=sigma)], y=[true_value, 0],  
                line=dict(shape='hv', color='green', width=3, dash='dash'), marker=dict(opacity=0),  
                name='True Value')

fig.show()
# fig.write_image("IS_samples.png")

/tmp/ipykernel_96/3417960681.py:27: RuntimeWarning:

invalid value encountered in divide



In [ ]:
fig = go.Figure()
fig.update_layout(
    xaxis=dict(
        showline=True, zeroline=True, linewidth=2, linecolor='black', mirror = True,
        showgrid=False, showticklabels=True, ticks="outside", tickfont=dict(size=15, family="times new roman", color='black'),
        title='Hazard Intensity - x', titlefont=dict(size=18, family="times new roman", color='black'),
        range=[0, 5]),
    yaxis=dict(
        showline=True, zeroline=True, linewidth=2, linecolor='black', mirror= True, side="left",
        showgrid=True, showticklabels=True, ticks="outside", tickfont_size=15,
        title='Loss Function - f(x)', titlefont=dict(size=18, family="times new roman", color='black'),  
        range=[0, 1]),
    yaxis2=dict(
        showline=True, zeroline=False, linewidth=2, linecolor='black',
        showgrid=False, showticklabels=False, 
        range=[0, 0.9]),
    showlegend = True,
    legend_font=dict(
        family="Times New Roman",
        size=18,
        color="black"),
    paper_bgcolor = 'rgba(0,0,0,0)',
    plot_bgcolor  = 'rgba(0,0,0,0)',
    height = 500,
    width  = 800)

fig.add_scatter(x=x, y=p(x)/q(x), marker=dict(color='black'), yaxis='y', name='weight')

fig.show()
# fig.write_image("weight_func.png")

/tmp/ipykernel_96/2735196141.py:27: RuntimeWarning:

invalid value encountered in divide



In [ ]:
fig = go.Figure()
fig.update_layout(
    xaxis=dict(
        showline=True, zeroline=True, linewidth=2, linecolor='black', mirror = True,
        showgrid=False, showticklabels=True, ticks="outside", tickfont=dict(size=15, family="times new roman", color='black'),
        title='Hazard Intensity - x', titlefont=dict(size=18, family="times new roman", color='black'),
        range=[0, 5]),
    yaxis=dict(
        showline=True, zeroline=True, linewidth=2, linecolor='black', mirror= True, side="left",
        showgrid=True, showticklabels=True, ticks="outside", tickfont_size=15,
        title='Loss Function - f(x)', titlefont=dict(size=18, family="times new roman", color='black'),  
        range=[0, 1]),
    yaxis2=dict(
        showline=True, zeroline=False, linewidth=2, linecolor='black',
        showgrid=False, showticklabels=False, 
        range=[0, 1.2]),
    showlegend = True,
    legend_font=dict(
        family="Times New Roman",
        size=18,
        color="black"),
    paper_bgcolor = 'rgba(0,0,0,0)',
    plot_bgcolor  = 'rgba(0,0,0,0)',
    height = 500,
    width  = 800)

fig.add_scatter(x=x, y=f(x), line=dict(dash='dot', color='black'), yaxis='y', name='f(x)')
fig.add_scatter(x=x, y=p(x),  line=dict(color='blue'), yaxis='y2', name='p(x)')
fig.add_scatter(x=x, y=p(x)*f(x)/true_value, line=dict(dash='dash', color='red'), yaxis='y2', name='q*(x)')

fig.show()
# fig.write_image("opt_IS_dist.png")

In [ ]:
fig = go.Figure()
fig.update_layout(
    xaxis=dict(
        showline=True, zeroline=True, linewidth=2, linecolor='black', mirror = True,
        showgrid=False, showticklabels=True, ticks="outside", tickfont=dict(size=15, family="times new roman", color='black'),
        title='Hazard Intensity - x', titlefont=dict(size=18, family="times new roman", color='black'),
        range=[0, 5]),
    yaxis=dict(
        showline=True, zeroline=True, linewidth=2, linecolor='black', mirror= True, side="left",
        showgrid=True, showticklabels=True, ticks="outside", tickfont_size=15,
        title='Loss Function - f(x)', titlefont=dict(size=18, family="times new roman", color='black'),  
        range=[0, 1]),
    yaxis2=dict(
        showline=True, zeroline=False, linewidth=2, linecolor='black',
        showgrid=False, showticklabels=False, 
        range=[0, 1.2]),
    showlegend = True,
    legend_font=dict(
        family="Times New Roman",
        size=15,
        color="black"),
    paper_bgcolor = 'rgba(0,0,0,0)',
    plot_bgcolor  = 'rgba(0,0,0,0)',
    height = 500,
    width  = 800)

fig.add_scatter(x=x, y=f(x), line=dict(dash='dot', color='black'), yaxis='y', name='f(x)')
fig.add_scatter(x=x, y=p(x),  line=dict(color='blue'), yaxis='y2', name='p(x)')
fig.add_scatter(x=x, y=p(x)*f(x)/true_value, line=dict(dash='dash', color='red'), yaxis='y2', name='q*(x)')

for i in range(len(MCMC_samples)):
    fig.add_scatter(x=[MCMC_samples[i]], y=[0],  mode='markers', line=dict(color='black', width=0.3), 
                    marker=dict(size=18, symbol='line-ns', line=dict(width=2.5, color="DarkSlateGrey")), 
                    yaxis='y', showlegend=False)

# kde = gaussian_kde(np.array(MCMC_samples).T, bw_method = 'silverman')
# fig.add_scatter(x=x, y=kde.evaluate(x), name='KDE fitted to MCMC samples', line=dict(color='green'), yaxis='y')

kde = sm.nonparametric.KDEUnivariate(MCMC_samples)
kde.fit(bw=0.2)
fig.add_scatter(x=kde.support, y=kde.density, name='KDE fitted to MCMC samples', mode='lines', line=dict(color='green'))

fig.show()
# fig.write_image("near_opt_IS_dist.png")

In [ ]:
fig = go.Figure()
fig.update_layout(
    xaxis=dict(
        showline=True, zeroline=True, linewidth=2, linecolor='black', mirror = True,
        showgrid=False, showticklabels=True, ticks="outside", tickfont=dict(size=15, family="times new roman", color='black'),
        title='Hazard Intensity - x', titlefont=dict(size=18, family="times new roman", color='black'),
        range=[0, 5]),
    yaxis=dict(
        showline=True, zeroline=True, linewidth=2, linecolor='black', mirror= True, side="left",
        showgrid=True, showticklabels=True, ticks="outside", tickfont_size=15,
        title='Loss Function - f(x)', titlefont=dict(size=18, family="times new roman", color='black'),  
        range=[0, 1]),
    yaxis2=dict(
        showline=True, zeroline=False, linewidth=2, linecolor='black',
        showgrid=False, showticklabels=False, 
        range=[0, 1.2]),
    showlegend = True,
    legend_font=dict(
        family="Times New Roman",
        size=15,
        color="black"),
    paper_bgcolor = 'rgba(0,0,0,0)',
    plot_bgcolor  = 'rgba(0,0,0,0)',
    height = 500,
    width  = 800)

kde = gaussian_kde(np.array(MCMC_samples).T, bw_method = 'silverman')
weighted_f = f(x)*p(x)/kde.evaluate(x)
weighted_f[kde.evaluate(x) <= 0.01] = 0

MCMC_IS_samples  = kde.resample(num_of_samples)[0] 
MCMC_IS_estimate = np.average(f(MCMC_IS_samples)*p(MCMC_IS_samples)/kde.evaluate(MCMC_IS_samples))

fig.add_scatter(x=x, y=kde.evaluate(x), name='KDE fitted to MCMC samples', line=dict(color='green'), yaxis='y2')
fig.add_scatter(x=x, y=weighted_f, name='weighted f(x)', line=dict(color='black', dash='dash'), yaxis='y')

KDE_f_of_x = f(MCMC_IS_samples)*p(MCMC_IS_samples)/kde.evaluate(MCMC_IS_samples)
for i in range(len(MCMC_IS_samples)):
    trace = go.Scatter(
        x=[MCMC_IS_samples[i], -1],
        y=[0, KDE_f_of_x[i]],
        line_shape='vh',
        line=dict(color='black', width=0.3),
        marker=dict(size=18, symbol='line-ns', line=dict(width=2.5, color="DarkSlateGrey")),
        yaxis='y',
        showlegend = False)    
    fig.add_trace(trace)

fig.add_scatter(x=[0], y=[np.average(MCMC_IS_estimate)], 
                mode='markers+text', 
                marker=dict(size=30, symbol='line-ew', line=dict(width=4.5, color='black')), 
                text = f'E[f(x)] = {np.round(np.average(MCMC_IS_estimate), 4)}', 
                textposition="top right", 
                textfont=dict(family="times new roman", size=15, color='black'), showlegend=False, yaxis='y')

fig.add_scatter(x=[0, norm.ppf(true_value, loc=mu+1, scale=sigma)], y=[true_value, 0],  
                line=dict(shape='hv', color='green', width=3, dash='dash'), marker=dict(opacity=0),  
                name='True Value', yaxis='y')
fig.show() 
# fig.write_image("MCMC_IS_samples.png")

/tmp/ipykernel_96/3199203626.py:28: RuntimeWarning:

divide by zero encountered in divide

/tmp/ipykernel_96/3199203626.py:28: RuntimeWarning:

invalid value encountered in divide



In [ ]:
# Main results
values = [[f'<b>Estimation</b><br>true_value = {true_value:0.3f}', '<b>Relative Error</b>'], 
          [MC_estimate, MC_error],
          [trunc_MC_estimate, trunc_MC_error],
          [IS_estimate, IS_error],
          [MCMC_IS_estimate, MCMC_IS_error]]

tabular_results = go.Figure(data=[go.Table(
    columnorder = [1, 2, 3, 4, 5],
    header = dict(
        values = [[''], ['<b>Crude Monte Carlo</b>'], ['<b>Truncated Monte Carlo</b>'], ['<b>Importance Sampling</b>'], ['<b>MCMC Importance Sampling</b>']],
        line_color='black',
        align=['left','center'],
        font=dict(size=14),
        height=40),
    cells=dict(
        values=values,
        line_color='black',
        fill=dict(color=['white']),
        align=['left', 'center'],
        font_size=14,
        height=30,
        format=['','0.3f','0.3f', '0.3f', '0.3f'])
)])
tabular_results.show()

In [ ]:
# Running parameters of MC
MC_running_mean  = []
MC_running_error = []

for i in range(100):
    num_of_samples = (i+1)*10 
    MC_estimates = []
    MC_errors    = []
    for j in range(50):
        MC_samples = get_MC_samples(num_of_samples)
        MC_estimates.append(np.average(f(MC_samples)))
        MC_errors.append(np.average(np.abs(f(MC_samples)-true_value)/true_value))

    MC_estimate = np.average(MC_estimates)
    MC_error    = np.average(MC_errors)
    
    MC_running_mean.append(MC_estimate)
    MC_running_error.append(MC_error)

# Running parameters of IS
IS_running_mean  = []
IS_running_error = []

for i in range(100):
    num_of_samples = (i+1)*10 
    IS_estimates = []
    IS_errors    = []
    for j in range(50):
        IS_samples = get_IS_samples(num_of_samples)
        IS_f_of_x  = f(IS_samples)*p(IS_samples)/q(IS_samples)
        IS_estimates.append(get_IS_estimate(num_of_samples, IS_samples))
        IS_errors.append(np.average(np.abs(IS_f_of_x-true_value)/true_value))

    IS_estimate = np.average(IS_estimates)
    IS_error    = np.average(IS_errors)
    
    IS_running_mean.append(IS_estimate)
    IS_running_error.append(IS_errors)

# Running parameters of MCMC_IS
MCMC_IS_running_mean  = []
MCMC_IS_running_error = []

for i in range(100):
    num_of_samples = (i+1)*10 
    MCMC_IS_estimates = []
    MCMC_IS_errors    = []
    for j in range(50):   
        MCMC_IS_samples = kde.resample(num_of_samples)[0]
        MCMC_IS_estimates.append(np.average(f(MCMC_IS_samples)*p(MCMC_IS_samples)/kde.evaluate(MCMC_IS_samples)))
        error = np.abs((f(MCMC_IS_samples)*p(MCMC_IS_samples)/kde.evaluate(MCMC_IS_samples))-true_value)/true_value
        MCMC_IS_errors.append(np.average(error))

    MCMC_IS_estimate = np.average(MCMC_IS_estimates)
    MCMC_IS_error    = np.average(MCMC_IS_errors)
    
    MCMC_IS_running_mean.append(MCMC_IS_estimate)
    MCMC_IS_running_error.append(MCMC_IS_error)


In [ ]:
fig = go.Figure()
fig.update_layout(
    xaxis=dict(
        showline=True, zeroline=True, linewidth=2, linecolor='black', mirror = True,
        showgrid=False, showticklabels=True, ticks="outside", tickfont=dict(size=15, family="times new roman", color='black'),
        title='Number of Samples', titlefont=dict(size=18, family="times new roman", color='black')),
    yaxis=dict(
        showline=True, zeroline=True, linewidth=2, linecolor='black', mirror= True, side="left",
        showgrid=True, showticklabels=True, ticks="outside", tickfont_size=15,
        title='Loss Estimation', titlefont=dict(size=18, family="times new roman", color='black')),
    showlegend = True,
    legend_font=dict(
        family="Times New Roman",
        size=17,
        color="black"),
    paper_bgcolor = 'rgba(0,0,0,0)',
    plot_bgcolor  = 'rgba(0,0,0,0)',
    height = 500,
    width  = 800)

####################################################################################
# Running mean 
running_mean = {'Monte Carlo':MC_running_mean,
                'Importance Sampling':IS_running_mean,
                'MCMC Importance Sampling':MCMC_IS_running_mean}

df = pd.DataFrame(running_mean, columns=['Monte Carlo',  
                                         'Importance Sampling', 'MCMC Importance Sampling'])
df['Number of Samples'] = [(i+1)*10 for i in range(100)]
df.set_index('Number of Samples', inplace=True)

fig.add_scatter(x=df.index, y = df['Monte Carlo'], mode = 'lines', 
                line=dict(dash='dot', color='black'), name='crude MC')
fig.add_scatter(x=df.index, y = df['Importance Sampling'], mode = 'lines', 
                line=dict(dash='dash', color='green'), name='traditional IS')
fig.add_scatter(x=df.index, y = df['MCMC Importance Sampling'], mode = 'lines', 
                line=dict(color='black'), name='MCMC-IS')

fig.show()
# fig.write_image("running_properties.png")

<a style='text-decoration:none;line-height:16px;display:flex;color:#5B5B62;padding:10px;justify-content:end;' href='https://deepnote.com?utm_source=created-in-deepnote-cell&projectId=1769d2a2-cc69-4c7c-a48d-a5310f119005' target="_blank">
 </img>
Created in <span style='font-weight:600;margin-left:4px;'>Deepnote</span></a>